In [1]:
import pandas as pd
from collections import OrderedDict
import numpy as np
import openpyxl
import os.path
from ast import literal_eval # for parsing list stored as string back into list
from save2Excel import save2Excel

/mnt/7ACA0CC0CA0C7B21/temp/py36/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
# directly loading grouped-by-trips file created in last program
df = pd.read_csv('grouped-tripwise.csv', dtype=str, index_col='sr').fillna('')
# typecasting all columns as text, so that concat etc operations are simpler to do further along.
print(df.shape)
df.columns

(35550, 36)


Index(['TRIP_ID', 'DEPOT_CODE', 'SERVICE_ID', 'SERVICE_NO', 'SERVICE_TYPE',
       'DAY_NIGHT_OUT', 'SCHEDULE_DAYS', 'ROUTE_ID', 'ROUTE_NUMBER',
       'TRIP_NUM', 'TRIP_TYPE', 'STAGE_ID', 'CURRENT_STAGE_NAME', 'num_stops',
       'STAGE_TYPE', 'DISTANCE', 'TIME_DISTANCE', 'FROM_TIME', 'first_time',
       'TO_TIME', 'BREAK_TIME', 'OPERATIONAL_DAYS', 'OD_MON', 'OD_TUE',
       'OD_WED', 'OD_THU', 'OD_FRI', 'OD_SAT', 'OD_SUN', 'FROM_TIME_num',
       'FROM_TIME_NEW', 'crossMidnight', 'timingsOK', 'gtfs_calendar_id',
       'gtfs_direction_id', 'trip_short_name'],
      dtype='object')

In [3]:
df.head()

TRIP_ID DEPOT_CODE SERVICE_ID SERVICE_NO SERVICE_TYPE DAY_NIGHT_OUT  \
sr                                                                       
0      100        KCG         60       0292           SN             D   
1   100059        MI2    6707965       2201           CS             D   
2   100060        MI2    6707965       2201           CS             D   
3   100081        MI2    6707965       2201           CS             D   
4   100082        MI2    6707965       2201           CS             D   

   SCHEDULE_DAYS ROUTE_ID ROUTE_NUMBER TRIP_NUM       ...       OD_FRI OD_SAT  \
sr                                                    ...                       
0              1      115           2J        7       ...            Y      Y   
1              2    18131         222L        1       ...            Y      Y   
2              2    18131         222L        2       ...            Y      Y   
3              2    18131         222L        3       ...            Y      Y   
4              2    18131         222L        4       ...            Y      Y   

   OD_SUN                                      FROM_TIME_num  \
sr                                                             
0       Y  [1235, 1239, 1243, 1248, 1252, 1257, 1261, 126...   
1       Y                          [454, 454, 454, 469, 469]   
2       Y                          [469, 469, 469, 559, 559]   
3       Y                          [589, 589, 679, 679, 679]   
4       Y                          [709, 709, 709, 799, 799]   

                                        FROM_TIME_NEW crossMidnight timingsOK  \
sr                                                                              
0   ['20:35', '20:39', '20:43', '20:48', '20:52', ...         False      True   
1       ['07:34', '07:34', '07:34', '07:49', '07:49']         False      True   
2       ['07:49', '07:49', '07:49', '09:19', '09:19']         False      True   
3       ['09:49', '09:49', '11:19', '11:19', '11:19']         False      True   
4       ['11:49', '11:49', '11:49', '13:19', '13:19']         False      True   

   gtfs_calendar_id gtfs_direction_id trip_short_name  
sr                                                     
0   @MoTuWeThFrSaSu                 1     2J: 20:35 D  
1   @MoTuWeThFrSaSu                 0   222L: 07:34 U  
2   @MoTuWeThFrSaSu                 0   222L: 07:49 U  
3   @MoTuWeThFrSaSu                 1   222L: 09:49 D  
4   @MoTuWeThFrSaSu                 0   222L: 11:49 U  

[5 rows x 36 columns]

## 1. Route to Service mapping

In [4]:
#services
servicesDF1 = df.drop_duplicates(['DEPOT_CODE','SERVICE_ID','SERVICE_NO'])
print(servicesDF1.shape)
servicesDF1

(4752, 36)


TRIP_ID DEPOT_CODE SERVICE_ID SERVICE_NO SERVICE_TYPE DAY_NIGHT_OUT  \
sr                                                                          
0         100        KCG         60       0292           SN             D   
1      100059        MI2    6707965       2201           CS             D   
9      100087        MI2    6707966       2301           CS             D   
17     100095        MI2    6707967       2401           CS             D   
25     100103        MI2    6707968       2501           CS             D   
33     100111        MI2    6707969       2601           CS             D   
41     100119        MI2    6707970       2701           CS             D   
49     100142        JDM   21566972       0211           CO             D   
50     100172        HN1    5296002       119D           ME             D   
63     100381        HN2    5231126       0301           CO             D   
70     100388        HN2    5231127       0302           CO             D   
79     100397        HN1    5295820       0292           SU             D   
88     101650        KGD    6732461       1731           SU             D   
91     101687        KGD    6732462       1732           SU             D   
94     101896        KGD    6732386       1181           CO             D   
95     102867        KGD    6732454       1701           CO             D   
103    102891        CNT   10767882       0371           ME             D   
104    102898        CNT   10767883       0372           ME             D   
106    102917        KGD    6732455       1702           CO             D   
115    102938        KGD    6732456       1711           CO             D   
123    102956        KGD    6758883       1712           CO             D   
132    102987        KGD   22763207       0042           CO             N   
145       103        KCG        248       1471           CO             D   
150    103149        KGD    7096543       003E           CO             N   
171    107523        KGD    6732271       008D           VR             D   
178    107554        KGD    6732272       008E           VR             D   
186    107731        KGD    8228461       011D           SN             D   
192    107769        KGD    8229160       011E           SN             D   
198    107830        KGD    6732289       017D           VR             D   
204    107901        KGD    6732322       0341           CO             D   
...       ...        ...        ...        ...          ...           ...   
35425   97381        HPT   10670799       1552           XC             D   
35433   97389        HPT   10670781       1451           XC             D   
35438   97399        HPT   10670782       1452           XC             D   
35444   97435        HPT   10670796       1541           CO             D   
35450   97453        HPT   10670797       1542           CO             D   
35457   97579        HPT   10670747       1251           SN             D   
35464   97586        HPT   10670748       1252           SN             D   
35471   97665        HPT   10670580       0171           PS             D   
35478   97686        HPT   10670756       1292           ME             N   
35490   97730        HPT   10670770       1392           CO             N   
35506   97762        HPT   10670769       1382           XS             N   
35521   97888        HPT   10670773       1411           SN             D   
35526   97894        HPT   10670774       1412           SN             D   
35531   97900        HPT   10670775       1421           SN             D   
35536   97905        HPT   10670776       1422           SN             D   
35541   97950        HPT   10670784       1481           SN             D   
35546   97955        HPT   10670785       1482           SN             D   
35551   97961        HPT   10670786       1491           SN             D   
35556   97966        HPT   10670787       1492           SN             D   
35

In [5]:
len( servicesDF1.SERVICE_ID.unique() )

4752

In [6]:
len( servicesDF1.SERVICE_NO.unique() )

711

In [7]:
# is the depot-service pair unique and corresponding to service id?
servicesDF2 = df.drop_duplicates(['DEPOT_CODE','SERVICE_NO'])
print(servicesDF2.shape)

(4752, 36)


In [8]:
# that settles it. So, let's make a listing by depot, route, service number

In [9]:
def parse_int(x):
    ''' 
    from https://gist.github.com/lsauer/6088767#gistcomment-2309011
    take just the initial numeric digits of a string and convert to number
    '''
    temp = []
    for c in str(x).strip():
        if c.isdigit():
            temp.append(c)
        else:
            break
    return int("".join(temp)) if "".join(temp) else ''

def serviceMappingFunction(x):
    names = {
        'service_no': list(set(x['SERVICE_NO'])),
        'num_service_no': len(set(x['SERVICE_NO'])),
        
        'service_id': list(set(x['SERVICE_ID'])),
        'num_service_id': len(set(x['SERVICE_ID'])),
        
        'num_service_types': len(set(x['SERVICE_TYPE'])),
        'num_trips': len(x),
        'route_numeric': parse_int(x.name[1])
    }
    return pd.Series(names, index=['service_no','num_service_no','service_id','num_service_id','num_service_types','num_trips','route_numeric'])

In [10]:
serviceMappingDF1 = df.groupby(['DEPOT_CODE','ROUTE_NUMBER']).apply(serviceMappingFunction)
serviceMappingDF1

service_no  \
DEPOT_CODE ROUTE_NUMBER                                                       
BGD        100R                                                [0242, 0302]   
           107V/R         [0341, 0862, 0342, 034D, 0861, 0851, 0852, 087...   
           117L                                    [0992, 0972, 0991, 0272]   
           156/299                                             [0351, 0352]   
           156B/118                                                  [0211]   
           156L                                    [1082, 1081, 1062, 1061]   
           158/277D                                                  [1141]   
           158F           [0132, 1111, 0162, 1102, 1121, 0131, 0152, 112...   
           158J/L                      [0731, 0741, 0732, 0721, 0742, 0722]   
           18R                         [0432, 0452, 0442, 0431, 0441, 0451]   
           1D/J                                    [1072, 0682, 0681, 1071]   
           1L             [1292, 1272, 1282, 1311, 1271, 1301, 1312, 128...   
           1M/D                                    [0321, 0362, 0031, 0322]   
           201                                           [0401, 0402, 0392]   
           201 G/I                                       [1332, 1331, 1322]   
           201M           [0421, 0422, 0091, 042E, 0412, 0381, 0411, 018...   
           217/300                                             [0881, 0961]   
           279                         [0651, 0601, 0641, 0631, 0611, 0621]   
           280            [0702, 069E, 077D, 070E, 057D, 077E, 0771, 067...   
           30/290U                     [0821, 0792, 0791, 0832, 0831, 0822]   
           300            [0592, 0591, 0912, 1042, 0941, 0931, 0911, 093...   
           526N/G                                                    [1321]   
           72J            [0101, 1162, 0061, 0071, 0051, 1172, 0371, 117...   
           90D/47Y                                             [0812, 0802]   
           90L                         [0761, 0192, 076E, 0191, 0762, 076D]   
           90L/290F                                                  [1131]   
           90N/U          [0022, 0012, 0011, 0951, 0142, 0952, 0462, 002...   
BHL        216W           [1332, 0081, 1301, 0632, 0631, 1302, 0082, 046...   
           218            [1442, 112E, 008E, 1111, 1022, 1112, 1441, 063...   
           218D/L         [1541, 1592, 1512, 1551, 1532, 1531, 1521, 158...   
...                                                                     ...   
UPL        113I/M         [0661, 0032, 0021, 0662, 0091, 0211, 1652, 113...   
           113I/V                                        [1381, 1321, 1351]   
           113K/L         [1521, 1022, 1522, 0872, 1482, 0892, 069D, 037...   
           113M           [1721, 0651, 1272, 0521, 051D, 1271, 0692, 081...   
           113M/W         [1541, 1512, 1532, 1531, 1491, 1511, 1492, 147...   
           113Y            [0442, 0081, 0441, 0492, 1162, 1161, 0062, 0072]   
           113Y/K         [1221, 1222, 2081, 0941, 1921, 1011, 1892, 190...   
           115            [0161, 0282, 0322, 0731, 0281, 1262, 0271, 026...   
           115C                                          [0291, 0952, 0292]   
           115M           [1742, 1872, 1871, 012D, 012E, 1741, 1752, 012...   
           18/219         [1172, 1292, 1282, 1142, 1121, 1171, 1122, 114...   
           18N                                                 [0351, 0352]   
           18V            [0542, 0101, 0301, 0541, 0102, 0981, 1621, 162...   
           245A                                                      [0182]   
           280                                                 [0591, 0592]   
           280B                                    [0622, 0612, 0621, 0601]   
           280E                                                [0532, 0531]   
           280N                                                [0501, 0502]   
           283S                     

In [11]:
serviceMappingDF2 = serviceMappingDF1.reset_index().sort_values(['DEPOT_CODE','route_numeric','ROUTE_NUMBER'])
serviceMappingDF2

DEPOT_CODE   ROUTE_NUMBER  \
10         BGD           1D/J   
11         BGD             1L   
12         BGD           1M/D   
9          BGD            18R   
19         BGD        30/290U   
22         BGD            72J   
23         BGD        90D/47Y   
24         BGD            90L   
25         BGD       90L/290F   
26         BGD          90N/U   
0          BGD           100R   
1          BGD         107V/R   
2          BGD           117L   
3          BGD        156/299   
4          BGD       156B/118   
5          BGD           156L   
6          BGD       158/277D   
7          BGD           158F   
8          BGD         158J/L   
13         BGD            201   
14         BGD        201 G/I   
15         BGD           201M   
16         BGD        217/300   
17         BGD            279   
18         BGD            280   
20         BGD            300   
21         BGD         526N/G   
27         BHL           216W   
28         BHL            218   
29         BHL         218D/L   
..         ...            ...   
808        UPL            18V   
822        UPL            71A   
823        UPL         90/251   
794        UPL           113A   
795        UPL        113I/KP   
796        UPL         113I/M   
797        UPL         113I/V   
798        UPL         113K/L   
799        UPL           113M   
800        UPL         113M/W   
801        UPL           113Y   
802        UPL         113Y/K   
803        UPL            115   
804        UPL           115C   
805        UPL           115M   
809        UPL           245A   
810        UPL            280   
811        UPL           280B   
812        UPL           280E   
813        UPL           280N   
814        UPL           283S   
815        UPL           284P   
816        UPL            300   
817        UPL        300/126   
818        UPL           490S   
819        UPL            493   
820        UPL            543   
821        UPL            545   
824        UPL  MGBS-TIRUPATI   
825        UPL            YGT   

                                            service_no  num_service_no  \
10                            [1072, 0682, 0681, 1071]               4   
11   [1292, 1272, 1282, 1311, 1271, 1301, 1312, 128...              14   
12                            [0321, 0362, 0031, 0322]               4   
9                 [0432, 0452, 0442, 0431, 0441, 0451]               6   
19                [0821, 0792, 0791, 0832, 0831, 0822]               6   
22   [0101, 1162, 0061, 0071, 0051, 1172, 0371, 117...              22   
23                                        [0812, 0802]               2   
24                [0761, 0192, 076E, 0191, 0762, 076D]               6   
25                                              [1131]               1   
26   [0022, 0012, 0011, 0951, 0142, 0952, 0462, 002...              10   
0                                         [0242, 0302]               2   
1    [0341, 0862, 0342, 034D, 0861, 0851, 0852, 087...               9   
2                             [0992, 0972, 0991, 0272]               4   
3                                         [0351, 0352]               2   
4                                               [0211]               1   
5                             [1082, 1081, 1062, 1061]               4   
6                                               [1141]               1   
7    [0132, 1111, 0162, 1102, 1121, 0131, 0152, 112...              13   
8                 [0731, 0741, 0732, 0721, 0742, 0722]               6   
13                                  [0401, 0402, 0392]               3   
14                                  [1332, 1331, 1322]               3   
15   [0421, 0422, 0091, 042E, 0412, 0381, 0411, 018...              10   
16                                        [0881, 0961]               2   
17                [0651, 0601, 0641, 0631, 0611, 0621]               6   
18   [0702, 069E, 077D, 070E, 057D, 077E, 0771, 067...              13   
20   [0592, 0591, 0912, 1042, 094

In [12]:
# checking for KCG..
# serviceMappingDF2[ serviceMappingDF2.DEPOT_CODE == 'KCG']
# nope, doesn't neatly tally with MTD141 data. But it's something to work from.

In [13]:
serviceMappingDF2.to_csv('route_service_mapping.csv',index=False)

In [14]:
save2Excel(serviceMappingDF2,'Route_service_mapping',indexlabel=False)

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating', 'Routes_sameDepot', 'Trips_OddTimings', 'TripLengths_grouping', 'serviceType_grouping']
Sheet Route_service_mapping added to TSRTC-analysis.xlsx


### > 1. Done.

In [15]:
'#'*100

'####################################################################################################'

## 2. Find: for one route_num with different route_id's, do they have same or different sequence of stops?

In [16]:
df.num_stops.unique()

array(['10', '5', '7', '18', '26', '21', '6', '13', '17', '23', '11',
       '36', '2', '16', '19', '15', '14', '30', '9', '25', '27', '4',
       '12', '24', '8', '20', '3', '53', '22', '29', '38', '34', '28',
       '33', '31', '37', '52', '42'], dtype=object)

In [17]:
def routeSequenceFunction(x):
    names = OrderedDict({
        'trips': list(set(x['TRIP_ID'])),
        'patterns_count': len(x),
        'num_stops': x['num_stops'].iloc[0], #its the same number, just using max to grab one 
        'TRIP_TYPE': x.TRIP_TYPE.iloc[0] if len(x.TRIP_TYPE.unique()) == 1 else x.TRIP_TYPE.unique().tolist(),
        'depots': x.DEPOT_CODE.unique()
        #'patterns_name': x.CURRENT_STAGE_NAME.unique(),
        #'patterns_id': x.STAGE_ID.unique(),
        #'num_patterns': len(x.STAGE_ID.unique())
    })
    return pd.Series(names)

In [18]:
routePattern1 = df.groupby(['ROUTE_NUMBER','ROUTE_ID','CURRENT_STAGE_NAME','STAGE_ID']).apply(routeSequenceFunction)
routePattern1

trips  \
ROUTE_NUMBER  ROUTE_ID CURRENT_STAGE_NAME                                 STAGE_ID                                                                                                
1             77       ['AFZAL-GUNJ', 'PLAY-GROUND', 'RAM-KOTI', 'CHIK... ['13260', '806', '1007', '14395', '1133', '182']    [546, 608, 565, 606, 557, 610, 597, 552, 559, ...   
                       ['SECUNDERABAD-RATHIFILE-BUS-STATION', 'MUSHEER... ['182', '1133', '14395', '1007', '806', '13260']    [592, 603, 562, 547, 553, 558, 566, 555, 564, ...   
10            8026     ['DUNDIGAL', 'JNTU-COLLEGE', 'RANIGUNJ', 'PLAZA... ['8158', '8305', '1049', '807', '820', '181', '...         [22076, 22001, 23462, 23460, 23465, 21995]   
                       ['DUNDIGAL', 'JNTU-COLLEGE', 'RANIGUNJ', 'PLAZA... ['8158', '8305', '1049', '807', '181', '820', '...                              [22070, 25276, 22024]   
                       ['DUNDIGAL', 'RANIGUNJ', 'JNTU-COLLEGE', 'PLAZA... ['8158', '1049', '8305', '807', '820', '181', '...                [23458, 21972, 21970, 21989, 21968]   
                       ['DUNDIGAL', 'RANIGUNJ', 'JNTU-COLLEGE', 'PLAZA... ['8158', '1049', '8305', '807', '181', '820', '...                       [21999, 21962, 22060, 22050]   
                       ['JNTU-COLLEGE', 'DUNDIGAL', 'RANIGUNJ', 'PLAZA... ['8305', '8158', '1049', '807', '820', '181', '...                       [21964, 22062, 21974, 22064]   
                       ['JNTU-COLLEGE', 'DUNDIGAL', 'RANIGUNJ', 'PLAZA... ['8305', '8158', '1049', '807', '181', '820', '...                [21960, 22006, 22074, 21958, 22012]   
                       ['JNTU-COLLEGE', 'RANIGUNJ', 'DUNDIGAL', 'PLAZA... ['8305', '1049', '8158', '807', '820', '181', '...         [22066, 23456, 22048, 23452, 23455, 23453]   
                       ['JNTU-COLLEGE', 'RANIGUNJ', 'DUNDIGAL', 'PLAZA... ['8305', '1049', '8158', '807', '181', '820', '...                                            [22068]   
                       ['RANIGUNJ', 'DUNDIGAL', 'JNTU-COLLEGE', 'PLAZA... ['1049', '8158', '8305', '807', '820', '181', '...                                     [22072, 21991]   
                       ['RANIGUNJ', 'DUNDIGAL', 'JNTU-COLLEGE', 'PLAZA... ['1049', '8158', '8305', '807', '181', '820', '...                [25270, 25272, 25269, 22016, 25274]   
                       ['RANIGUNJ', 'JNTU-COLLEGE', 'DUNDIGAL', 'PLAZA... ['1049', '8305', '8158', '807', '820', '181', '...                              [22010, 22014, 22022]   
                       ['RANIGUNJ', 'JNTU-COLLEGE', 'DUNDIGAL', 'PLAZA... ['1049', '8305', '8158', '807', '181', '820', '...                                     [21997, 22026]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '820', '181', '8...                                     [21961, 22013]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '820', '181', '8...                                     [22065, 22007]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '820', '181', '8...  [21996, 23466, 23464, 25273, 25275, 25271, 23467]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '820', '181', '8...                                            [23459]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '820', '181', '8...         [21971, 21973, 21967, 21969, 22071, 22005]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '820', '181', '8...         [22049, 22027, 23454, 23457, 22017, 22051]   
                       ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY-... ['142', '7640', '294', '3623', '181', '820', '8...                                     [22073, 22002]   
                       ['SANATH-NAGAR', 'KUKATPALLY',

In [19]:
routePattern2 = routePattern1.reset_index().rename(columns={'CURRENT_STAGE_NAME':'pattern_name', 'STAGE_ID':'pattern_id'})
routePattern2

ROUTE_NUMBER ROUTE_ID  \
0                 1       77   
1                 1       77   
2                10     8026   
3                10     8026   
4                10     8026   
5                10     8026   
6                10     8026   
7                10     8026   
8                10     8026   
9                10     8026   
10               10     8026   
11               10     8026   
12               10     8026   
13               10     8026   
14               10     8026   
15               10     8026   
16               10     8026   
17               10     8026   
18               10     8026   
19               10     8026   
20               10     8026   
21               10     8026   
22               10     8026   
23               10     8026   
24               10     8026   
25              100     7471   
26              100     7471   
27             100D    24589   
28             100D    24589   
29             100D    24589   
...             ...      ...   
5964     PALAMANERU    14250   
5965     PALAMANERU    14250   
5966     PALAMANERU    14250   
5967     PALAMANERU    14250   
5968     PALAMANERU    14250   
5969     PALAMANERU    14250   
5970           PCPL     7427   
5971           PCPL     7427   
5972    PULIVENDULA    11608   
5973    PULIVENDULA    11608   
5974    THADIPATHRI    12478   
5975    THADIPATHRI    12478   
5976     VIJAYAWADA     9646   
5977     VIJAYAWADA     9646   
5978            VJA    10027   
5979            VJA    10027   
5980            VJA     9780   
5981            VJA     9780   
5982            VJA     9997   
5983            VJA     9997   
5984       VJA-ATNR     9831   
5985       VJA-ATNR     9831   
5986       WARANGAL    11014   
5987       WARANGAL    11014   
5988  WARANGAL-BMRM    11027   
5989  WARANGAL-BMRM    11027   
5990   WARANGAL-PCM    11026   
5991   WARANGAL-PCM    11026   
5992            YGT     6601   
5993            YGT     6601   

                                           pattern_name  \
0     ['AFZAL-GUNJ', 'PLAY-GROUND', 'RAM-KOTI', 'CHI...   
1     ['SECUNDERABAD-RATHIFILE-BUS-STATION', 'MUSHEE...   
2     ['DUNDIGAL', 'JNTU-COLLEGE', 'RANIGUNJ', 'PLAZ...   
3     ['DUNDIGAL', 'JNTU-COLLEGE', 'RANIGUNJ', 'PLAZ...   
4     ['DUNDIGAL', 'RANIGUNJ', 'JNTU-COLLEGE', 'PLAZ...   
5     ['DUNDIGAL', 'RANIGUNJ', 'JNTU-COLLEGE', 'PLAZ...   
6     ['JNTU-COLLEGE', 'DUNDIGAL', 'RANIGUNJ', 'PLAZ...   
7     ['JNTU-COLLEGE', 'DUNDIGAL', 'RANIGUNJ', 'PLAZ...   
8     ['JNTU-COLLEGE', 'RANIGUNJ', 'DUNDIGAL', 'PLAZ...   
9     ['JNTU-COLLEGE', 'RANIGUNJ', 'DUNDIGAL', 'PLAZ...   
10    ['RANIGUNJ', 'DUNDIGAL', 'JNTU-COLLEGE', 'PLAZ...   
11    ['RANIGUNJ', 'DUNDIGAL', 'JNTU-COLLEGE', 'PLAZ...   
12    ['RANIGUNJ', 'JNTU-COLLEGE', 'DUNDIGAL', 'PLAZ...   
13    ['RANIGUNJ', 'JNTU-COLLEGE', 'DUNDIGAL', 'PLAZ...   
14    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
15    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
16    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
17    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
18    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
19    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
20    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
21    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
22    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
23    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
24    ['SANATH-NAGAR', 'KUKATPALLY', 'SANJEEVA-REDDY...   
25    ['JANA-PRIYA-MAHA-NAGAR', 'DILSUKH-NAGAR', 'SE...   
26    ['SECUNDERABAD-RATHIFILE-BUS-STATION', 'DILSUK...   
27    ['KOTI-WOMENS-COLLEGE', 'MIDHANI-DEPOT', 'MIDH...   
28    ['KOTI-WOMENS-COLLEGE', 'MIDHANI-DEPOT', 'SAI-...   
29    ['RAJIV-GRUHA-KALPA', 'TIRUMAL-NAGAR', 'BN-RED...   
...                                                 ...   
5964  ['MAHATMA-GANDHI-BUS-STATION-IMLIBUN', 'MADENA...   
5965  ['PALAMANERU', 'KARNOOL', 'ANATHAPUR', 'KACHIG...   
5966  ['PALAMANE

In [20]:
len(routePattern2.ROUTE_NUMBER.unique())

695

In [21]:
len(routePattern2.ROUTE_ID.unique())

833

In [22]:
save2Excel(routePattern2, 'Route_patterns', indexlabel='sr')

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating', 'Routes_sameDepot', 'Trips_OddTimings', 'TripLengths_grouping', 'serviceType_grouping', 'Route_service_mapping']
Sheet Route_patterns added to TSRTC-analysis.xlsx


### > 2. Done.
There are totally 5994 patterns under various routes.  
If each route_id had only 2 patters : one for UP and one for DOWN, then there would be 1666 patterns.

In [23]:
'#'*100

'####################################################################################################'

### 3. flipping routePattern2 : group by pattern and see if multiple routes come under it

In [24]:
def patternGroupFunction(x):
    flattenedRow = OrderedDict({
        'ROUTE_NUMBER': x.ROUTE_NUMBER.unique(),
        'ROUTE_ID': x.ROUTE_ID.unique(),
        'num_routes': len(x.ROUTE_NUMBER.unique())
    })
    return pd.Series(flattenedRow)

In [25]:
routePattern3 = routePattern2.groupby('pattern_name').apply(patternGroupFunction)
#routePattern3

In [26]:
routePattern3[ routePattern3.num_routes > 1]

ROUTE_NUMBER  ROUTE_ID  \
pattern_name                                                                
['AFZAL-GUNJ', 'PLAY-GROUND', 'RAM-KOTI', 'CHIK...      [1, 1P]  [77, 78]   
['SECUNDERABAD-RATHIFILE-BUS-STATION', 'MUSHEER...      [1, 1P]  [77, 78]   

                                                    num_routes  
pattern_name                                                    
['AFZAL-GUNJ', 'PLAY-GROUND', 'RAM-KOTI', 'CHIK...           2  
['SECUNDERABAD-RATHIFILE-BUS-STATION', 'MUSHEER...           2

In [27]:
# quickly checking for id's:
routePattern4 = routePattern2.groupby('pattern_id').apply(patternGroupFunction)
routePattern4[ routePattern4.num_routes > 1]
# nah, same.

ROUTE_NUMBER  ROUTE_ID  \
pattern_id                                                                
['13260', '806', '1007', '14395', '1133', '182']      [1, 1P]  [77, 78]   
['182', '1133', '14395', '1007', '806', '13260']      [1, 1P]  [77, 78]   

                                                  num_routes  
pattern_id                                                    
['13260', '806', '1007', '14395', '1133', '182']           2  
['182', '1133', '14395', '1007', '806', '13260']           2

### > 3. Done.
There is one pair of up-down patterns, that are found repeating in two routes: 1,1P

In [28]:
'#'*100

'####################################################################################################'

## 4. Pattern counts per route

In [29]:
# getting that into a table
def patternsCountFunction(x):
    flattenedRow = OrderedDict({
        'num_patterns':len(x),
        'Ups': len(x[x.TRIP_TYPE=='U']),
        'Downs': len(x[x.TRIP_TYPE=='D']),
        'route_numeric': parse_int(x.name[0]),
        'route_ids': x.ROUTE_ID.iloc[0] if len(x.ROUTE_ID.unique())==1 else x.ROUTE_ID.unique(),
        'depots': x.depots.apply(lambda y: y[0]).unique()
    })
    return pd.Series(flattenedRow)

In [30]:
routePattern5 = routePattern2.groupby(['ROUTE_NUMBER']).apply(patternsCountFunction)\
    .reset_index().sort_values(['num_patterns','route_numeric','ROUTE_NUMBER'],ascending=[False,True,True])
routePattern5

ROUTE_NUMBER  num_patterns  Ups  Downs route_numeric  \
323                       250C           188  100     88             2   
445                         3K           182   87     95             3   
365                        280           163   84     79             2   
182                       195W           143   79     64             1   
9                         102B           135   68     67             1   
399                        290           132   66     66             2   
267                        219           122   67     55             2   
352                        25M           101   49     52             2   
91                        127K            93   48     45             1   
105                    156/299            90   45     45             1   
63                        113M            89   42     47             1   
48                        10KM            87   49     38             1   
62                      113K/L            71   37     34             1   
424                         30            71   35     36             3   
110                       158F            70   36     34             1   
258                       217A            70   35     35             2   
191                        19M            68   34     34             1   
353                        25S            68   35     33             2   
566                        66G            66   34     32             6   
265                       218L            64   36     28             2   
75                        116N            62   32     30             1   
371                       280R            62   37     25             2   
138                       171M            55   27     28             1   
41                       10H/L            54   40     14             1   
661  ECIL X ROADS TO GHATKESAR            51   31     20                 
177                       193M            50   28     22             1   
120                        15H            47   24     23             1   
40                     10H/25I            46   43      3             1   
525                        532            46   23     23             5   
417                        29R            43   22     21             2   
..                         ...           ...  ...    ...           ...   
186                      19F/A             1    1      0             1   
189                       19KA             1    1      0             1   
327                    251J SU             1    1      0             2   
330                    251M SU             1    1      0             2   
331                       251P             1    1      0             2   
332                      251SS             1    1      0             2   
391                     288N/B             1    0      1             2   
421                         2U             1    1      0             2   
455                        449             1    1      0             4   
456                       44EX             1    1      0             4   
457                        450             1    1      0             4   
461                        453             1    1      0             4   
462                        454             1    1      0             4   
526                     532 HK             1    1      0             5   
583                         73             1    1      0             7   
584                         74             1    1      0             7   
608                        8AU             1    1      0             8   
617                        90K             1    0      1             9   
625                         92             1    1      0             9   
626                        92A             1    1      0             9   
627                        92S             1    1      0             9   
628                      94/95             1    1      0             9   
630                   

In [31]:
# saving to analysis sheet
save2Excel(routePattern5,'Route_pattern_counts',indexlabel=False)

Existing sheets in TSRTC-analysis.xlsx : ['Stops_Repeating', 'Stops_Grouping', 'ServiceType_Stops', 'Route_id_depot_listing', 'Routes_repeating', 'Routes_sameDepot', 'Trips_OddTimings', 'TripLengths_grouping', 'serviceType_grouping', 'Route_service_mapping', 'Route_patterns']
Sheet Route_pattern_counts added to TSRTC-analysis.xlsx


### > 4. Done.
Route 250C, UP direction has the max number of varying patterns.

In [32]:
'#'*100

'####################################################################################################'

## 5. Which routes have just one Up and one Down pattern?

In [33]:
routePattern6 = routePattern5[ (routePattern5.Ups ==1) & (routePattern5.Downs ==1)]
routePattern6

ROUTE_NUMBER  num_patterns  Ups  Downs route_numeric route_ids depots
0                  1             2    1      1             1        77  [KCG]
2                100             2    1      1             1      7471  [DSR]
4               100R             2    1      1             1      6335  [BGD]
5             101K/D             2    1      1             1     28949  [MDN]
7           102/253L             2    1      1             1     11905  [MHM]
10         102B/218L             2    1      1             1      5924  [MDN]
15              102W             2    1      1             1      6047  [MDN]
19         104M/127K             2    1      1             1      5948  [MDN]
21         104R/127K             2    1      1             1      5982  [MDN]
22         104R/218L             2    1      1             1      5923  [MDN]
23              104S             2    1      1             1      5945  [MDN]
26             107JD             2    1      1             1      5288  [CNT]
27             107JS             2    1      1             1      5226  [CNT]
28          107JS-XC             2    1      1             1      9672  [CNT]
30             107VR             2    1      1             1      7390  [DSR]
31          107VR-ME             2    1      1             1      5235  [CNT]
32          107VR-SN             2    1      1             1      5289  [CNT]
34              10AS             2    1      1             1      9983  [KPL]
35              10BK             2    1      1             1      8166  [RN2]
42              10HA             2    1      1             1      5553  [HCU]
44             10K/L             2    1      1             1      9851  [MI1]
45             10K/P             2    1      1             1     10834  [MI2]
46              10KB             2    1      1             1      9842  [MI1]
47              10KJ             2    1      1             1      8170  [RN2]
49               10L             2    1      1             1      9832  [MI1]
52              10YF             2    1      1             1      8172  [RN2]
53              10YH             2    1      1             1      5256  [CNT]
56              113F             2    1      1             1      8459  [CCL]
57           113I/KP             2    1      1             1      6606  [UPL]
58            113I/M             2    1      1             1      6564  [UPL]
..               ...           ...  ...    ...           ...       ...    ...
655             BGLR             2    1      1                    9781  [BHL]
656            BLANK             2    1      1                   16390  [CCL]
657             CHVL             2    1      1                    5874  [MPM]
658              CPL             2    1      1                    6072  [HN1]
659             CTPL             2    1      1                    6115  [HN2]
662  ECIL-AMALAPURAM             2    1      1                   10403  [KGD]
663      ECIL-GUNTUR             2    1      1                   10397  [KGD]
664      ECIL-RAZOLE             2    1      1                   11646  [KGD]
665         ECIL-TPT             2    1      1                   10395  [KGD]
667           KADAPA             2    1      1                    9947  [KCG]
668              KNL             2    1      1                   27009  [BHL]
669               KP             2    1      1                   18909  [KPL]
670               M1             2    1      1                   29219  [RN2]
671       MARKAPURAM             2    1      1                    9648  [DSR]
672    MGBS-TIRUPATI             2    1      1                   11786  [UPL]
676          MYP-NZB             2    1      1                   10022  [MI1]
677          MYP-VJA             2    1      1                    9827  [MI1]
678         MYP-WGLL             2    1      1                   10023  [MI1]
680   NIZAMABAD-ARSP             2    1      1                   11047  [MPM]
681   NIZAMABAD-MBRK          

In [34]:
routePattern6.depots.value_counts()

[MPM]    36
[KGD]    30
[FMA]    28
[CNT]    28
[HN1]    25
[MHM]    24
[MI1]    23
[UPL]    20
[BGD]    16
[HN2]    16
[JDM]    15
[BHL]    14
[RN2]    13
[DSR]    13
[HCU]    12
[CCL]    11
[MDN]    10
[KCG]     9
[MS1]     7
[RN1]     7
[HPT]     6
[KPL]     5
[RJN]     4
[BKP]     4
[MI2]     3
[MS2]     3
[FNR]     2
Name: depots, dtype: int64

### > 5. Done.
Out of 695, there are 384 routes that have just one Up pattern and one Down pattern. MPM depot has max, 36 such "proper" routes.

## 6. routes having only one direction

In [35]:
onlyUpDF = routePattern5[ (routePattern5.Downs ==0)]
print(len(onlyUpDF),'routes have only Up direction:\n',onlyUpDF.ROUTE_NUMBER.unique())

36 routes have only Up direction:
 ['22R' '455' '78' '95M' '120K' '14X' '16X' '188/251' '188H' '19F/A' '19KA'
 '251J SU' '251M SU' '251P' '251SS' '2U' '449' '44EX' '450' '453' '454'
 '532 HK' '73' '74' '8AU' '92' '92A' '92S' '94/95' '94K' '94R' '94U' '95N'
 '95P' '95R' 'MP-NZB']


In [36]:
onlyDownDF = routePattern5[ (routePattern5.Ups ==0)]
print(len(onlyDownDF),'routes have only Down direction:\n',onlyDownDF.ROUTE_NUMBER.unique())

3 routes have only Down direction:
 ['288N/B' '90K' 'DVRM']


#### depots having most of these single-direction routes:

In [37]:
routePattern5[ (routePattern5.Downs ==0) | (routePattern5.Ups ==0) ].depots.value_counts()

[RJN]    28
[CNT]     3
[FNR]     2
[MPM]     2
[MDN]     2
[HPT]     1
[KCG]     1
Name: depots, dtype: int64

### > 6. Done. 
There are 36 routes having only Down direction and 3 routes having only Up direction.  
28 of these are under RJN depot.  
Putting this in anomalies section

In [38]:
'#'*100

'####################################################################################################'